# 유동인구 데이터 정제

## 1. 라이브러리 & 데이터

In [1]:
import pandas as pd
import numpy as np
import zipfile
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
warnings.filterwarnings('ignore')
pd.set_option('display.max_columns',100)
pd.set_option('display.max_rows',300)

### 데이터셋 불러오기

In [2]:
# ZIP 파일 경로 (외부 ZIP 파일)
zip_file_path = '../data/성심당 전체데이터.zip'

# 2023년 데이터 저장할 딕셔너리 생성
pop_data = {}

# 2023년 데이터 불러오기
with zipfile.ZipFile(zip_file_path, 'r') as outer_zip:
    with outer_zip.open('people.zip') as inner_zip_file:
        with zipfile.ZipFile(inner_zip_file) as inner_zip:
            for month in range(7, 13):  # 2023년 7월부터 12월까지
                file_name = f'50CELL_DJJUNGGU_2023{month:02d}.csv'
                if file_name in inner_zip.namelist():
                    var_name = f'pop2023{month:02d}'  # 딕셔너리 키 생성
                    with inner_zip.open(file_name) as file:
                        pop_data[var_name] = pd.read_csv(file)

# 2024년 데이터 불러오기
with zipfile.ZipFile(zip_file_path, 'r') as outer_zip:
    with outer_zip.open('people.zip') as inner_zip_file:
        with zipfile.ZipFile(inner_zip_file) as inner_zip:
            for month in range(1, 7):  # 2024년 1월부터 6월까지
                file_name = f'50CELL_DJJUNGGU_2024{month:02d}.csv'
                if file_name in inner_zip.namelist():
                    var_name = f'pop2024{month:02d}'  # 딕셔너리 키 생성
                    with inner_zip.open(file_name) as file:
                        pop_data[var_name] = pd.read_csv(file)

In [3]:
유동인구정의서 = pd.read_csv("../data/유동인구정의서.csv") ; 카드매출정의서 = pd.read_csv("../data/카드매출정의서.csv")
상권정보_데이터코드 = pd.read_csv("../data/상권정보_데이터코드.csv") ; 상권정보_업종분류 = pd.read_csv("../data/상권정보_업종분류.csv")
국토조사 = pd.read_csv('../data/국토지리정보원_국토조사_(격자)500M.csv')
업종 = pd.read_csv("../data/업종코드.csv") ; hdong = pd.read_csv("../data/행정동코드.csv")

### 행정동코드 데이터 전처리

In [4]:
hdong['행정동코드'] = hdong['행정동코드'].astype(str).str[:-2].astype(int)
hdong['시군구코드'] = hdong['행정동코드'].astype(str).str[:-3].astype(int)
hdong['시도코드'] = hdong['시군구코드'].astype(str).str[:-3].astype(int)
# 앞자리가 51인 경우에만 42로 변경하는 함수 정의
def replace_prefix_51_with_42(column):
    return column.apply(lambda x: int('42' + str(x)[2:]) if str(x).startswith('51') else x)

# 행정동코드, 시도코드, 시군구코드 열의 앞자리가 51인 경우만 변경
hdong['행정동코드'] = replace_prefix_51_with_42(hdong['행정동코드'])
hdong['시도코드'] = replace_prefix_51_with_42(hdong['시도코드'])
hdong['시군구코드'] = replace_prefix_51_with_42(hdong['시군구코드'])

In [5]:
관광지 = pd.read_csv("../data/관광지목록.csv")

## 2. 전처리

### 컬럼명 변경

In [6]:
# 유동인구정의서에서 '항목 설명' 열을 가져오기
new_columns = 유동인구정의서['항목 설명'].values

# pop_data 안의 모든 데이터프레임의 컬럼 이름을 변경
for df_name in pop_data:
    pop_data[df_name].columns = new_columns

In [7]:
# pop_data에서 'pop202307'부터 'pop202406'까지의 데이터프레임 이름 가져오기
pop_dfs = [f"pop20230{i}" for i in range(7, 10)] + [f"pop20240{i}" for i in range(1, 7)]

# 각 데이터프레임에서 열을 가져오고, 셀번호 중복 행을 제거한 후 합치기
combined_df = pd.DataFrame()

for df_name in pop_dfs:
    # pop_data에서 데이터프레임을 가져오기
    df = pop_data[df_name]
    
    # 열 선택 및 중복된 셀번호 행 제거
    df_filtered = df[['셀번호', 'x좌표', 'y좌표', "행정동코드"]].drop_duplicates(subset='셀번호')
    
    # 합치기
    combined_df = pd.concat([combined_df, df_filtered], ignore_index=True)

# 최종 합친 데이터프레임에서 셀번호 중복 행 다시 제거
final_df = combined_df.drop_duplicates(subset='셀번호')
final_df = final_df.merge(hdong[['행정동코드', "읍면동명"]], how="left", left_on="행정동코드", right_on="행정동코드")
final_df = final_df.drop_duplicates(subset='셀번호').reset_index()

In [8]:
#final_df.to_csv("cell.csv", index=False)

## 3. 지도 그리기

In [9]:
from geopy.distance import geodesic
import pandas as pd
import numpy as np
import folium
from tqdm import tqdm
from pyproj import Proj, Transformer

tqdm.pandas()  # pandas의 tqdm 확장 활성화

# KATEC 좌표계와 WGS84 좌표계 정의
WGS84 = {'proj': 'latlong', 'datum': 'WGS84', 'ellps': 'WGS84'}
KATEC = {'proj': 'tmerc', 'lat_0': '38N', 'lon_0': '128E', 
         'ellps': 'bessel', 'x_0': 400000, 'y_0': 600000,
         'k': 0.9999, 'units': 'm',
         'towgs84': '-115.80,474.99,674.11,1.16,-2.31,-1.63,6.43'}

# KATEC -> WGS84 변환 함수
def KATEC_to_wgs84(x, y):
    transformer = Transformer.from_proj(Proj(**KATEC), Proj(**WGS84), always_xy=True)
    lon, lat = transformer.transform(x, y)
    return lat, lon

# 좌표 변환 적용 (progress_apply를 통해 진행 바 표시)
final_df[['latitude', 'longitude']] = final_df.progress_apply(lambda row: KATEC_to_wgs84(row['x좌표'], row['y좌표']), axis=1, result_type='expand')

# 변환된 좌표를 지도에 표시
m = folium.Map(location=[final_df['latitude'].mean(), final_df['longitude'].mean()], zoom_start=15)

# 각 좌표에 검은 점 추가 (팝업 제거, 점 크기 조정)
for _, row in tqdm(final_df.iterrows(), total=len(final_df)):
    folium.CircleMarker(
        location=[row['latitude'], row['longitude']],
        radius=1,  # 점의 크기
        color='black',  # 점의 색깔
        fill=True,
        fill_opacity=1
    ).add_to(m)

# 관광지명과 반경 100미터 표시 및 점의 개수 계산
tourist_counts = []
tourist_points = []  # 반경 내 점들의 셀번호를 저장할 리스트

for _, row in 관광지.iterrows():
    # 관광지명 마커 추가
    folium.Marker(
        location=[row['Latitude'], row['Longitude']],
        popup=row['관광지명']
    ).add_to(m)
    
    lat = row['Latitude']
    lon = row['Longitude']

    # 반경 100미터 원 추가
    folium.Circle(
        location=[lat, lon],
        radius=100,
        color='red',
        fill=True,
        fill_color='red',
        fill_opacity=0.3,
        weight=1,
    ).add_to(m)

    # 관광지와 셀 간 거리 계산하여 반경 100미터 내 셀번호 저장
    within_radius_cell = []
    for _, cell_row in final_df.iterrows():
        distance = geodesic((lat, lon), (cell_row['latitude'], cell_row['longitude'])).meters
        if distance <= 100:
            within_radius_cell.append(cell_row['셀번호'])  # 100m 이내의 셀번호 저장
    
    count = len(within_radius_cell)  # 반경 내 점의 개수

    # 결과 저장
    tourist_counts.append({'관광지명': row['관광지명'], '점 개수': count})
    tourist_points.append({'관광지명': row['관광지명'], '셀번호': within_radius_cell})

# 점 개수와 셀번호 데이터프레임으로 정리
tourist_counts_df = pd.DataFrame(tourist_counts)
tourist_points_df = pd.DataFrame(tourist_points)

# 결과 출력
#tourist_counts_df, tourist_points_df

# 지도를 HTML 파일로 저장 (필요할 경우 활성화) (figure 폴더 참고)
#m.save('성심당 반경 100m 유동인구.html')

# Jupyter Notebook에서 사용하는 경우, 지도 바로 출력
#m


100%|██████████| 10933/10933 [00:00<00:00, 19625.88it/s]


In [10]:
m

In [11]:
# tourist_counts_df, tourist_points_df, 관광지 세 개의 데이터프레임을 '관광지명'을 기준으로 병합
tour = pd.merge(tourist_counts_df, tourist_points_df, on='관광지명', how='inner')
tour = pd.merge(tour, 관광지, on='관광지명', how='inner')

In [12]:
# tour.to_csv("tour.csv", index=False)

# 데이터 합치기

In [13]:
# pop_data 안의 각 데이터프레임에 적용할 함수
def group_age_columns(df):
    # 남성 연령대 그룹화
    df['남성_10대'] = df[['남성10~14', '남성15~19']].sum(axis=1)
    df['남성_20대'] = df[['남성20~24', '남성25~29']].sum(axis=1)
    df['남성_30대'] = df[['남성30~34', '남성35~39']].sum(axis=1)
    df['남성_40대'] = df[['남성40~44', '남성45~49']].sum(axis=1)
    df['남성_50대'] = df[['남성50~54', '남성55~59']].sum(axis=1)
    df['남성_60대'] = df[['남성60~64', '남성65~69']].sum(axis=1)
    df['남성_70대이상'] = df[['남성70세 이상']].sum(axis=1)

    # 여성 연령대 그룹화
    df['여성_10대'] = df[['여성10~14', '여성15~19']].sum(axis=1)
    df['여성_20대'] = df[['여성20~24', '여성25~29']].sum(axis=1)
    df['여성_30대'] = df[['여성30~34', '여성35~39']].sum(axis=1)
    df['여성_40대'] = df[['여성40~44', '여성45~49']].sum(axis=1)
    df['여성_50대'] = df[['여성50~54', '여성55~59']].sum(axis=1)
    df['여성_60대'] = df[['여성60~64', '여성65~69']].sum(axis=1)
    df['여성_70대이상'] = df[['여성70세 이상']].sum(axis=1)

    # 불필요한 원본 컬럼 삭제
    columns_to_drop = [
        '남성10세미만', '남성10~14', '남성15~19', '남성20~24', '남성25~29', '남성30~34', '남성35~39', 
        '남성40~44', '남성45~49', '남성50~54', '남성55~59', '남성60~64', '남성65~69', '남성70세 이상', 
        '여성10세미만', '여성10~14', '여성15~19', '여성20~24', '여성25~29', '여성30~34', '여성35~39', 
        '여성40~44', '여성45~49', '여성50~54', '여성55~59', '여성60~64', '여성65~69', '여성70세 이상'
    ]
    df.drop(columns=columns_to_drop, inplace=True)

# pop_data 안의 모든 데이터프레임에 연령대 그룹화를 적용
pop_data_keys = ['pop202307', 'pop202308', 'pop202309', 'pop202310', 'pop202311', 'pop202312', 
                 'pop202401', 'pop202402', 'pop202403', 'pop202404', 'pop202405', 'pop202406']

for key in pop_data_keys:
    group_age_columns(pop_data[key])

# 결과 확인 (예시로 pop202307 데이터프레임 확인)
#print(pop_data['pop202307'].head())

## 1. 봄

In [14]:
from pandas.tseries.holiday import USFederalHolidayCalendar as calendar

# 데이터 합치기
popdata_combined_spring = pd.concat([pop_data['pop202403'], pop_data['pop202404'], pop_data['pop202405']], ignore_index=True)

# 날짜 변수(일자)를 datetime 타입으로 변환
popdata_combined_spring['일자'] = pd.to_datetime(popdata_combined_spring['일자'], format='%Y%m%d')

# 공휴일 계산 (예시로 미국 공휴일을 사용, 한국 공휴일은 따로 처리해야 함)
cal = calendar()
holidays = cal.holidays(start=popdata_combined_spring['일자'].min(), end=popdata_combined_spring['일자'].max())

# '휴일' 변수 생성: 토, 일요일 또는 공휴일이면 '휴일', 그렇지 않으면 '평일'
popdata_combined_spring['holiday'] = popdata_combined_spring['일자'].apply(lambda x: '휴일' if x.weekday() >= 5 or x in holidays else '평일')

# 'time_period' 변수 생성: 시간대를 오전, 점심, 오후, 저녁, 심야로 분류
def time_to_period(hour):
    if 6 <= hour < 11:
        return '오전'
    elif 11 <= hour < 15:
        return '점심'
    elif 15 <= hour < 18:
        return '오후'
    elif 18 <= hour < 22:
        return '저녁'
    else:
        return '심야'

# '시간대' 변수를 시간대 범주로 변환
popdata_combined_spring['time_period'] = popdata_combined_spring['시간대'].apply(time_to_period)

In [15]:
# 필요한 남성 및 여성 연령대 컬럼
columns_to_median = [
    '남성_10대', '남성_20대', '남성_30대', '남성_40대', '남성_50대', '남성_60대', '남성_70대이상',
    '여성_10대', '여성_20대', '여성_30대', '여성_40대', '여성_50대', '여성_60대', '여성_70대이상'
]

# 관광지명별로 데이터를 그룹핑하고 중앙값 계산
result_list = []

for _, row in tour.iterrows():
    # 각 관광지명에 해당하는 셀번호 리스트
    cell_numbers = row['셀번호']
    
    # popdata_combined에서 해당 셀번호들에 해당하는 데이터 필터링
    filtered_data = popdata_combined_spring[popdata_combined_spring['셀번호'].isin(cell_numbers)]
    
    # 'holiday', 'time_period'별로 그룹핑하여 남녀 연령대별 인구의 중앙값 계산
    grouped_data = filtered_data.groupby(['holiday', 'time_period'])[columns_to_median].median().reset_index()
    
    # 관광지명 열 추가
    grouped_data['관광지명'] = row['관광지명']
    
    # 결과를 리스트에 저장
    result_list.append(grouped_data)

# 결과를 하나의 데이터프레임으로 병합
final_result_spring = pd.concat(result_list, ignore_index=True)

In [16]:
# 관광지명별로 그룹핑된 데이터를 가공하여 열 이름을 결합한 형태로 변환하는 코드

# 필요한 남성 및 여성 연령대 컬럼
columns_to_median = [
    '남성_10대', '남성_20대', '남성_30대', '남성_40대', '남성_50대', '남성_60대', '남성_70대이상',
    '여성_10대', '여성_20대', '여성_30대', '여성_40대', '여성_50대', '여성_60대', '여성_70대이상'
]

# 그룹핑된 데이터프레임을 넓은 형식으로 변환하는 함수
def create_wide_format(df):
    wide_format = df.pivot_table(
        index='관광지명',
        columns=['holiday', 'time_period'],
        values=columns_to_median
    )
    
    # MultiIndex를 단일 컬럼으로 변환 (열 이름을 "holiday_time_period_컬럼명" 형식으로 변환)
    wide_format.columns = [f'{h}_{t}_{col}' for h, t, col in wide_format.columns]
    
    # 인덱스를 초기화하여 관광지명을 열로 변환
    wide_format.reset_index(inplace=True)
    
    return wide_format

# 주어진 데이터로 넓은 형식의 데이터프레임 생성
final_result_wide_spring = create_wide_format(final_result_spring)
final_result_wide_spring.rename(columns=lambda x: '봄_' + x if x != '관광지명' else x, inplace=True)

In [17]:
#final_result_wide_spring.to_csv("final_result_spring.csv", index=False)

## 2. 여름

In [18]:
from pandas.tseries.holiday import USFederalHolidayCalendar as calendar

# 데이터 합치기
popdata_combined_summer = pd.concat([pop_data['pop202307'], pop_data['pop202308'], pop_data['pop202406']], ignore_index=True)

# 날짜 변수(일자)를 datetime 타입으로 변환
popdata_combined_summer['일자'] = pd.to_datetime(popdata_combined_summer['일자'], format='%Y%m%d')

# 공휴일 계산 (예시로 미국 공휴일을 사용, 한국 공휴일은 따로 처리해야 함)
cal = calendar()
holidays = cal.holidays(start=popdata_combined_summer['일자'].min(), end=popdata_combined_summer['일자'].max())

# '휴일' 변수 생성: 토, 일요일 또는 공휴일이면 '휴일', 그렇지 않으면 '평일'
popdata_combined_summer['holiday'] = popdata_combined_summer['일자'].apply(lambda x: '휴일' if x.weekday() >= 5 or x in holidays else '평일')

# 'time_period' 변수 생성: 시간대를 오전, 점심, 오후, 저녁, 심야로 분류
def time_to_period(hour):
    if 6 <= hour < 11:
        return '오전'
    elif 11 <= hour < 15:
        return '점심'
    elif 15 <= hour < 18:
        return '오후'
    elif 18 <= hour < 22:
        return '저녁'
    else:
        return '심야'

# '시간대' 변수를 시간대 범주로 변환
popdata_combined_summer['time_period'] = popdata_combined_summer['시간대'].apply(time_to_period)

In [19]:
# 필요한 남성 및 여성 연령대 컬럼
columns_to_median = [
    '남성_10대', '남성_20대', '남성_30대', '남성_40대', '남성_50대', '남성_60대', '남성_70대이상',
    '여성_10대', '여성_20대', '여성_30대', '여성_40대', '여성_50대', '여성_60대', '여성_70대이상'
]

# 관광지명별로 데이터를 그룹핑하고 중앙값 계산
result_list = []

for _, row in tour.iterrows():
    # 각 관광지명에 해당하는 셀번호 리스트
    cell_numbers = row['셀번호']
    
    # popdata_combined에서 해당 셀번호들에 해당하는 데이터 필터링
    filtered_data = popdata_combined_summer[popdata_combined_summer['셀번호'].isin(cell_numbers)]
    
    # 'holiday', 'time_period'별로 그룹핑하여 남녀 연령대별 인구의 중앙값 계산
    grouped_data = filtered_data.groupby(['holiday', 'time_period'])[columns_to_median].median().reset_index()
    
    # 관광지명 열 추가
    grouped_data['관광지명'] = row['관광지명']
    
    # 결과를 리스트에 저장
    result_list.append(grouped_data)

# 결과를 하나의 데이터프레임으로 병합
final_result_summer = pd.concat(result_list, ignore_index=True)

In [20]:
# 관광지명별로 그룹핑된 데이터를 가공하여 열 이름을 결합한 형태로 변환하는 코드

# 필요한 남성 및 여성 연령대 컬럼
columns_to_median = [
    '남성_10대', '남성_20대', '남성_30대', '남성_40대', '남성_50대', '남성_60대', '남성_70대이상',
    '여성_10대', '여성_20대', '여성_30대', '여성_40대', '여성_50대', '여성_60대', '여성_70대이상'
]

# 그룹핑된 데이터프레임을 넓은 형식으로 변환하는 함수
def create_wide_format(df):
    wide_format = df.pivot_table(
        index='관광지명',
        columns=['holiday', 'time_period'],
        values=columns_to_median
    )
    
    # MultiIndex를 단일 컬럼으로 변환 (열 이름을 "holiday_time_period_컬럼명" 형식으로 변환)
    wide_format.columns = [f'{h}_{t}_{col}' for h, t, col in wide_format.columns]
    
    # 인덱스를 초기화하여 관광지명을 열로 변환
    wide_format.reset_index(inplace=True)
    
    return wide_format

# 주어진 데이터로 넓은 형식의 데이터프레임 생성
final_result_wide_summer = create_wide_format(final_result_summer)
final_result_wide_summer.rename(columns=lambda x: '여름_' + x if x != '관광지명' else x, inplace=True)

In [21]:
#final_result_wide_summer.to_csv("final_result_summer.csv", index=False)

## 3. 가을

In [22]:
from pandas.tseries.holiday import USFederalHolidayCalendar as calendar

# 데이터 합치기
popdata_combined_fall = pd.concat([pop_data['pop202309'], pop_data['pop202310'], pop_data['pop202311']], ignore_index=True)

# 날짜 변수(일자)를 datetime 타입으로 변환
popdata_combined_fall['일자'] = pd.to_datetime(popdata_combined_fall['일자'], format='%Y%m%d')

# 공휴일 계산 (예시로 미국 공휴일을 사용, 한국 공휴일은 따로 처리해야 함)
cal = calendar()
holidays = cal.holidays(start=popdata_combined_fall['일자'].min(), end=popdata_combined_fall['일자'].max())

# '휴일' 변수 생성: 토, 일요일 또는 공휴일이면 '휴일', 그렇지 않으면 '평일'
popdata_combined_fall['holiday'] = popdata_combined_fall['일자'].apply(lambda x: '휴일' if x.weekday() >= 5 or x in holidays else '평일')

# 'time_period' 변수 생성: 시간대를 오전, 점심, 오후, 저녁, 심야로 분류
def time_to_period(hour):
    if 6 <= hour < 11:
        return '오전'
    elif 11 <= hour < 15:
        return '점심'
    elif 15 <= hour < 18:
        return '오후'
    elif 18 <= hour < 22:
        return '저녁'
    else:
        return '심야'

# '시간대' 변수를 시간대 범주로 변환
popdata_combined_fall['time_period'] = popdata_combined_fall['시간대'].apply(time_to_period)

In [23]:
# 필요한 남성 및 여성 연령대 컬럼
columns_to_median = [
    '남성_10대', '남성_20대', '남성_30대', '남성_40대', '남성_50대', '남성_60대', '남성_70대이상',
    '여성_10대', '여성_20대', '여성_30대', '여성_40대', '여성_50대', '여성_60대', '여성_70대이상'
]

# 관광지명별로 데이터를 그룹핑하고 중앙값 계산
result_list = []

for _, row in tour.iterrows():
    # 각 관광지명에 해당하는 셀번호 리스트
    cell_numbers = row['셀번호']
    
    # popdata_combined에서 해당 셀번호들에 해당하는 데이터 필터링
    filtered_data = popdata_combined_fall[popdata_combined_fall['셀번호'].isin(cell_numbers)]
    
    # 'holiday', 'time_period'별로 그룹핑하여 남녀 연령대별 인구의 중앙값 계산
    grouped_data = filtered_data.groupby(['holiday', 'time_period'])[columns_to_median].median().reset_index()
    
    # 관광지명 열 추가
    grouped_data['관광지명'] = row['관광지명']
    
    # 결과를 리스트에 저장
    result_list.append(grouped_data)

# 결과를 하나의 데이터프레임으로 병합
final_result_fall = pd.concat(result_list, ignore_index=True)

In [24]:
# 관광지명별로 그룹핑된 데이터를 가공하여 열 이름을 결합한 형태로 변환하는 코드

# 필요한 남성 및 여성 연령대 컬럼
columns_to_median = [
    '남성_10대', '남성_20대', '남성_30대', '남성_40대', '남성_50대', '남성_60대', '남성_70대이상',
    '여성_10대', '여성_20대', '여성_30대', '여성_40대', '여성_50대', '여성_60대', '여성_70대이상'
]

# 그룹핑된 데이터프레임을 넓은 형식으로 변환하는 함수
def create_wide_format(df):
    wide_format = df.pivot_table(
        index='관광지명',
        columns=['holiday', 'time_period'],
        values=columns_to_median
    )
    
    # MultiIndex를 단일 컬럼으로 변환 (열 이름을 "holiday_time_period_컬럼명" 형식으로 변환)
    wide_format.columns = [f'{h}_{t}_{col}' for h, t, col in wide_format.columns]
    
    # 인덱스를 초기화하여 관광지명을 열로 변환
    wide_format.reset_index(inplace=True)
    
    return wide_format

# 주어진 데이터로 넓은 형식의 데이터프레임 생성
final_result_wide_fall = create_wide_format(final_result_fall)
final_result_wide_fall.rename(columns=lambda x: '가을_' + x if x != '관광지명' else x, inplace=True)

In [25]:
#final_result_wide_fall.to_csv("final_result_fall.csv", index=False)

## 4. 겨울

In [26]:
from pandas.tseries.holiday import USFederalHolidayCalendar as calendar

# 데이터 합치기
popdata_combined_winter = pd.concat([pop_data['pop202312'], pop_data['pop202401'], pop_data['pop202402']], ignore_index=True)

# 날짜 변수(일자)를 datetime 타입으로 변환
popdata_combined_winter['일자'] = pd.to_datetime(popdata_combined_winter['일자'], format='%Y%m%d')

# 공휴일 계산 (예시로 미국 공휴일을 사용, 한국 공휴일은 따로 처리해야 함)
cal = calendar()
holidays = cal.holidays(start=popdata_combined_winter['일자'].min(), end=popdata_combined_winter['일자'].max())

# '휴일' 변수 생성: 토, 일요일 또는 공휴일이면 '휴일', 그렇지 않으면 '평일'
popdata_combined_winter['holiday'] = popdata_combined_winter['일자'].apply(lambda x: '휴일' if x.weekday() >= 5 or x in holidays else '평일')

# 'time_period' 변수 생성: 시간대를 오전, 점심, 오후, 저녁, 심야로 분류
def time_to_period(hour):
    if 6 <= hour < 11:
        return '오전'
    elif 11 <= hour < 15:
        return '점심'
    elif 15 <= hour < 18:
        return '오후'
    elif 18 <= hour < 22:
        return '저녁'
    else:
        return '심야'

# '시간대' 변수를 시간대 범주로 변환
popdata_combined_winter['time_period'] = popdata_combined_winter['시간대'].apply(time_to_period)

In [27]:
# 필요한 남성 및 여성 연령대 컬럼
columns_to_median = [
    '남성_10대', '남성_20대', '남성_30대', '남성_40대', '남성_50대', '남성_60대', '남성_70대이상',
    '여성_10대', '여성_20대', '여성_30대', '여성_40대', '여성_50대', '여성_60대', '여성_70대이상'
]

# 관광지명별로 데이터를 그룹핑하고 중앙값 계산
result_list = []

for _, row in tour.iterrows():
    # 각 관광지명에 해당하는 셀번호 리스트
    cell_numbers = row['셀번호']
    
    # popdata_combined에서 해당 셀번호들에 해당하는 데이터 필터링
    filtered_data = popdata_combined_winter[popdata_combined_winter['셀번호'].isin(cell_numbers)]
    
    # 'holiday', 'time_period'별로 그룹핑하여 남녀 연령대별 인구의 중앙값 계산
    grouped_data = filtered_data.groupby(['holiday', 'time_period'])[columns_to_median].median().reset_index()
    
    # 관광지명 열 추가
    grouped_data['관광지명'] = row['관광지명']
    
    # 결과를 리스트에 저장
    result_list.append(grouped_data)

# 결과를 하나의 데이터프레임으로 병합
final_result_winter = pd.concat(result_list, ignore_index=True)

In [28]:
# 관광지명별로 그룹핑된 데이터를 가공하여 열 이름을 결합한 형태로 변환하는 코드

# 필요한 남성 및 여성 연령대 컬럼
columns_to_median = [
    '남성_10대', '남성_20대', '남성_30대', '남성_40대', '남성_50대', '남성_60대', '남성_70대이상',
    '여성_10대', '여성_20대', '여성_30대', '여성_40대', '여성_50대', '여성_60대', '여성_70대이상'
]

# 그룹핑된 데이터프레임을 넓은 형식으로 변환하는 함수
def create_wide_format(df):
    wide_format = df.pivot_table(
        index='관광지명',
        columns=['holiday', 'time_period'],
        values=columns_to_median
    )
    
    # MultiIndex를 단일 컬럼으로 변환 (열 이름을 "holiday_time_period_컬럼명" 형식으로 변환)
    wide_format.columns = [f'{h}_{t}_{col}' for h, t, col in wide_format.columns]
    
    # 인덱스를 초기화하여 관광지명을 열로 변환
    wide_format.reset_index(inplace=True)
    
    return wide_format

# 주어진 데이터로 넓은 형식의 데이터프레임 생성
final_result_wide_winter = create_wide_format(final_result_winter)
final_result_wide_winter.rename(columns=lambda x: '겨울_' + x if x != '관광지명' else x, inplace=True)

In [29]:
#final_result_wide_winter.to_csv("final_result_winter.csv", index=False)

# 데이터 모두 합치기

In [30]:
final_result_wide_spring = pd.read_csv("../data/result/final_result_spring.csv")
final_result_wide_summer = pd.read_csv("../data/result/final_result_summer.csv")
final_result_wide_fall = pd.read_csv("../data/result/final_result_fall.csv")
final_result_wide_winter = pd.read_csv("../data/result/final_result_winter.csv")

In [31]:
최종 = 관광지.merge(final_result_wide_spring, how="left", left_on="관광지명", right_on="관광지명")
최종 = 최종.merge(final_result_wide_summer, how="left", left_on="관광지명", right_on="관광지명")
최종 = 최종.merge(final_result_wide_fall, how="left", left_on="관광지명", right_on="관광지명")
최종 = 최종.merge(final_result_wide_winter, how="left", left_on="관광지명", right_on="관광지명")

In [32]:
# 유동인구가 없는 NaN 값을 0으로 채우기
최종.fillna(0, inplace=True)

In [33]:
# 최종.to_csv("final.csv", index=False)

# 관광지 데이터 확인

In [34]:
pd.read_csv("../data/result/final.csv")

관광지명                            도로명주소   Latitude   Longitude  \
0       우리들공원                대전 중구 중앙로138번길 30  36.327067  127.425290   
1       대전오월드                   대전 중구 사정공원로 70  36.292342  127.395880   
2   한화생명이글스파크  대전 중구 대종로 373 한밭종합운동장 한화생명이글스파크  36.317079  127.429135   
3     대전아쿠아리움                 대전 중구 보문산공원로 469  36.309922  127.420705   
4        뿌리공원              대전 중구 뿌리공원로 79 뿌리공원  36.285427  127.388083   
5   대전근현대사전시관                    대전 중구 중앙로 101  36.326746  127.420376   
6        문창시장               대전 중구 문창로10번길 45-0  36.315484  127.438391   
7    으능정이문화거리               대전광역시 중구 은행동 48-14  36.329086  127.427670   
8        사정공원                대전 중구 사정공원로 160-0  36.297529  127.406583   
9        테미오래                대전 중구 보문로205번길 13  36.320558  127.423064   
10     성심당문화원                 대전 중구 중교로73번길 11  36.327094  127.427402   
11       태평시장              대전 중구 평촌로105번길 62-0  36.325441  127.397638   
12      서대전공원        대전광역시 중구 문화1동 계룡로904번길 30  36.320964  127.411548   
13    대전예술가의집             대전 중구 중앙로 32 대전예술가의집  36.322299  127.416055   
14        보문산              대전 중구 보문산공원로 426-83  36.311389  127.422484   
15     중촌시민공원               대전광역시 중구 중촌동 259-1  36.342947  127.405096   
16       테미공원             대전 중구 보문로199번길 37-36  36.319176  127.421831   
17  대전목재문화체험장                 대전 중구 보문산공원로 442  36.309770  127.423434   
18     유천종합시장             대전 중구 계백로1584번길 28-0  36.316727  127.396086   
19       산성시장                 대전 중구 대둔산로 420-0  36.306562  127.387155   
20     양지근린공원                대전 중구 선화서로29번길 20  36.326394  127.417755   
21    아신극장/1관             대전 중구 대종로 458 2층, 3층  36.325595  127.427914   
22        형통사      대전 중구 보문산공원로497번길 81-10 형통사  36.310084  127.419434   
23   커먼즈필드/대전                  대전 중구 중앙로 85 1층  36.326746  127.420376   
24    중앙로지하상가    대전 중구 중앙로 125-2 중앙로지하상가 관리사무소  36.327117  127.421529   
25   테미예술창작센터                    대전 중구 대종로 525  36.330326  127.423387   
26      상상아트홀          대전 중구 대종로505번길 28 상상아트홀  36.328805  127.423426   
27     대전보훈공원              대전 중구 보훈로 46 대전보훈공원  36.299564  127.399190   
28       대흥공원                 대전 중구 대종로460번길 8  36.325688  127.428423   
29    대전음악창작소          대전 중구 대흥로175번길 25 홍명프리존  36.326221  127.430460   
30        성심당             대전광역시 중구 대종로480번길 15  36.327681  127.427314   
31   성심당케익부띠끄                 대전광역시 중구 대종로 480  36.327540  127.426821   
32      대전형무소                     대전 중구 목중로 34  36.337130  127.410402   
33        유회당              대전 중구 운남로85번길 32-20  36.278793  127.408336   
34      창계숭절사               대전 중구 대둔산로137번길 67  36.284338  127.372390   
35        봉소루                    대전 중구 봉소루로 29  36.309181  127.440889   

    봄_남성_10대_평일_심야  봄_남성_10대_평일_오전  봄_남성_10대_평일_오후  봄_남성_10대_평일_저녁  \
0             1.04            0.00           0.140            0.11   
1             0.00            0.31           0.060            0.02   
2             0.00            0.00           0.070            0.05   
3             0.00            0.00           0.000            0.00   
4             0.00            0.00           0.000            0.00   
5             0.00            0.00           0.000            0.00   
6             0.08            0.08           0.160            0.24   
7             0.00            0.00           1.490            2.30   
8             0.00            0.00           0.000            0.00   
9             0.24            2.25           1.440            0.84   
10            0.24            0.14           1.470            1.89   
11            0.18            0.18           0.760            0.99   
12            1.17            0.98           3.675            4.87   
13            0.20            0.19           0.280            0.56   
14            0.00            0.00           0.000            0.00   
15            0.07            0.00           0.040            0.04   
16            0.08            0.10           0.090            0.08   
17            0.00            0.05           0.

In [35]:
#pip freeze > requirments.txt